In [58]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from sklearn.preprocessing import MinMaxScaler
import plotly.express as px
import plotly.graph_objects as go
import plotly.io as pio

%matplotlib inline

In [59]:
df = pd.read_csv("../data/FAO coffee bean production/coffee-bean-production.csv")
# df.drop(columns="Unnamed: 0",inplace=True)

In [60]:
df.columns = ["Entity", "Code", "Year", "Production"]

In [61]:
china_production = df.loc[df["Entity"] == "China", "Production"]
taiwan_production = df.loc[df["Entity"] == "Taiwan", ["Year", "Production"]]
china_year_mask = df["Year"].isin(taiwan_production["Year"])
df.loc[
    china_year_mask & (df["Entity"] == "China"), "Production"
] += taiwan_production.loc[
    taiwan_production["Year"].isin(df.loc[china_year_mask, "Year"]), "Production"
].values

In [62]:
df.loc[df["Entity"] == "China", "Production"]

1007      1612.00
1008      1756.00
1009      2042.00
1010      2346.00
1011      2577.00
          ...    
1063    115110.14
1064    116519.00
1065    121012.00
1066    114970.00
1067    108906.00
Name: Production, Length: 61, dtype: float64

In [63]:
df = df.drop(index=df[df["Entity"].isin(["Taiwan"])].index)
delete_name = [name for name in df.Entity.unique() if "(FAO)" in name]
continent = ["Africa", "Asia", "Oceania", "Americas", "Europe"]
df = df.drop(index=df[df["Entity"].isin(delete_name)].index)
df = df.drop(index=df[df["Entity"].isin(continent)].index)
mask = df.isna().any(axis=1)
no_code = list(df[mask].Entity.unique())
df = df.drop(index=df[df["Entity"].isin(no_code)].index)

In [64]:
df

Entity Code  Year  Production
183     Angola  AGO  1961   168600.00
184     Angola  AGO  1962   185000.00
185     Angola  AGO  1963   168300.00
186     Angola  AGO  1964   198200.00
187     Angola  AGO  1965   205000.00
...        ...  ...   ...         ...
7091  Zimbabwe  ZWE  2017      683.33
7092  Zimbabwe  ZWE  2018      627.78
7093  Zimbabwe  ZWE  2019      670.37
7094  Zimbabwe  ZWE  2020      660.49
7095  Zimbabwe  ZWE  2021      652.88

[5026 rows x 4 columns]

In [65]:
continent_df = px.data.gapminder()
continent_df = continent_df[["country", "continent"]]
continent_df = continent_df.rename(columns={"country": "Entity"})
new_df = pd.merge(df, continent_df, on="Entity", how="left").drop_duplicates()

In [66]:
data = new_df

In [67]:
import plotly.graph_objects as go
import plotly.express as px
import plotly.io as pio
import plotly.subplots as sp

# Create a subplot grid with 2 rows and 1 column
fig = sp.make_subplots(
    rows=1, cols=2,
    specs=[[{'type': 'choropleth'}, {'type': 'scatter'}]],
    subplot_titles=('World map', 'Coffee Production Over Time'))

continents = ['World', 'Africa', 'Americas', 'Asia', 'Europe']  # 5
years = df['Year'].unique()  # 61

colors = ["#527A18", "#678D38", "#E9BA4E", "#BF8C31", "#6E3D19"]

custom_scale = [[i/(len(colors)-1), colors[i]] for i in range(len(colors))]
# ADD A CHOROPLETH TRACES FOR THE DATA-FRAME
# use a double loop to iterate each continent and for every year, add a trace.

for continent in continents:
    for year in years:
        fig.add_trace(  # Add A trace to the figure
            go.Choropleth(  # Specify the type of the trace
                # uid=unique id (Assign an ID to the trace)
                uid=f"{continent}_{year}",
                # Supply location information tag for mapping
                locations=df[(df["Year"] == year) & (
                    df["continent"] == continent)]["Code"],
                # Data to be color-coded on graph
                z=np.log(df[(df["Year"] == year) & (
                    df["continent"] == continent)]["Production"]),
                colorbar=dict(
                    title="Production",
                    x=0.45,  # Adjust the x position of the color bar
                    xanchor='left',  # Anchor the color bar to the left
                    y=0.55,  # Adjust the y position of the color bar
                    yanchor='middle'  # Anchor the color bar in the middle
                ),
                visible=False,  # Specify whether or not to make data-visible when rendered
                zmin=0,  # Minimum value for the color scale
                zmax=np.log(5000000),  # Maximum value for the color scale
                colorscale=custom_scale,
                # Modify hover text to show original values
                hovertemplate="%{location}<br>Production: %{customdata:,}<extra></extra> tons",
                customdata=df[(df["Year"] == year)]["Production"]
            ), row=1, col=1
        )

for continent in continents:
    df_ct_tmp = df[df['continent'] == continent]
    production = []
    for year in years:
        df_ct_year_tmp = df_ct_tmp[df_ct_tmp["Year"] <= year]
        fig.add_trace(
            go.Scatter(
                uid=f"{continent}_line_{year}",
                x=pd.to_datetime(df["Year"], format="%Y").dt.year,
                y=df_ct_year_tmp.groupby('Year')["Production"].agg("sum"),
                mode='lines+markers',
                showlegend=False,
                name=f'{continent}',
                hovertemplate=f"{continent} Production ({year}):<br>" + " %{y:,} <extra></extra> tons",
            ), row=1, col=2
        )
        
fig.update_yaxes(row=1, col=2, tickformat=".3s")
# now, use another double for loop to add slider and button
# buttons
buttons = []
sliders = []
i = 0
j = 0
steps = []
for continent in continents:
    steps = []
    for year in years:
        step = dict(
            method="update",
            args=[{"visible": [False]*len(fig.data)}],  # layout attribute
            label=f'{year}'
        )
        step["args"][0]["visible"][i] = True
        step["args"][0]["visible"][i+305] = True
        i += 1
        steps.append(step)

    slider = [dict(
        active=0,
        currentvalue={"prefix": "Year: "},
        steps=steps
    )]
    sliders.append(slider)

    tmp = dict(
        label=str(continent),
        method="update",
        args=[{"visible": [False]*len(fig.data)}, {"sliders": slider}]
    )

    tmp["args"][0]["visible"][j*61] = True
    tmp["args"][0]["visible"][j*61+305] = True
    buttons.append(tmp)
    j += 1

updatemenus = [dict(
    buttons=buttons,
    direction="right",
    showactive=True,  # HIGHLIGHTS ACTIVE DROPDOWN ITEM OR ACTIVE BUTTON IF TRUE
    pad={"r": 10, "t": 10},  # PADDING
    x=0.00,  # POSITION
    y=1.2,
    xanchor="left",  # ANCHOR POINT
    yanchor="top"
)]


fig.data[0].visible = True
fig.data[307].visible = True
# update the layout
fig.update_layout(updatemenus=updatemenus, 
                  sliders=sliders[0], 
                  geo=dict(bgcolor='#F3EFE6'),
                  paper_bgcolor='#F3EFE6',
                  plot_bgcolor='#F3EFE6',
                  margin=dict(l=10, r=10) )


# SHOW
fig.show()

pio.write_html(fig, file=f'../website/pages/map_line.html', auto_open=False)

KeyError: 'continent'

In [ ]:
len(df.Entity.unique())

87

In [ ]:
np.sum(df[df["continent"] == "World"].groupby(["Year"])["Production"].sum().to_list())

781135081.31

In [ ]:
import plotly.graph_objects as go
import plotly.express as px
import plotly.io as pio
import plotly.subplots as sp
from functools import partial

# Create a subplot grid with 1 row and 2 columns
fig = sp.make_subplots(rows=1, cols=2, specs=[[{'type': 'choropleth'}, {'type': 'bar'}]],
                       subplot_titles=('World map', 'Coffee Production by Country'))

years = df['Year'].unique()

colors = ["#527A18", "#678D38", "#E9BA4E", "#BF8C31", "#6E3D19"]

custom_scale = [[i/(len(colors)-1), colors[i]] for i in range(len(colors))]

# Add Choropleth traces
for year in years:
    fig.add_trace(
        go.Choropleth(
            uid=f"world_{year}",
            locations=df[df["Year"] == year]["Code"],
            z=np.log(df[df["Year"] == year]["Production"]),
            colorbar=dict(
                title="Production",
                x=0.45,
                xanchor='left',
                y=0.55,
                yanchor='middle'
            ),
            visible=False,
            zmin=0,
            zmax=np.log(5000000),
            colorscale=custom_scale,
            hovertemplate="%{location}<br>Production: %{customdata:,}<extra></extra> tons",
            customdata=df[df["Year"] == year]["Production"]
        ), row=1, col=1
    )

# Add bar traces for each year
for year in years:
    # Sort the data frame by production in descending order
    df_year_sorted = df[df["Year"] == year].sort_values("Production", ascending=False)
    
    fig.add_trace(
        go.Bar(
            uid=f"bar_{year}",
            x=df_year_sorted["Entity"],
            y=df_year_sorted["Production"],
            visible=False,
            text=df_year_sorted["Production"],
            textposition='auto',
            hovertemplate="Country: %{x}<br>Production: %{y:,}<extra></extra> tons",
            width=0.8  # Make the bars wider
        ), row=1, col=2
    )

fig.update_yaxes(range=[0, max(df["Production"]) * 1.1], row=1, col=2)
# Make the first choropleth and bar plot trace visible
fig.data[0].visible = True
fig.data[len(years)].visible = True

# Create steps for the slider
steps = []
for i, year in enumerate(years):
    step = dict(
        method="animate",
        args=[{"visible": [False] * (2 * len(years)), 
               'frame': {'duration': 300, 'redraw': True},
                'mode': 'immediate',
                'transition': {'duration': 300}}],
        label=f"{year}"
    )
    step["args"][0]["visible"][i] = True
    step["args"][0]["visible"][i + len(years)] = True
    steps.append(step)

# Define the slider
sliders = [dict(
    active=0,
    currentvalue={"prefix": "Year: "},
    steps=steps,
    transition= {'duration': 300, 'easing': 'cubic-in-out'},
    pad={"t": 50}
)]

# Update the layout with the slider and animation settings
fig.update_layout(
    sliders=sliders,
    updatemenus=[{
        'buttons': [
            {
                'args': [None, {'frame': {'duration': 300, 'redraw': False},
                         'fromcurrent': True, 'transition': {'duration': 300, 'easing': 'quadratic-in-out'}}],
                'label': 'Play',
                'method': 'animate'
            },
            {
                'args': [[None], {'frame': {'duration': 0, 'redraw': False}, 'mode': 'immediate',
                'transition': {'duration': 0}}],
                'label': 'Pause',
                'method': 'animate'
            }
        ],
        'direction': 'left',
        'pad': {'r': 10, 't': 87},
        'showactive': False,
        'type': 'buttons',
        'x': 0.16,
        'xanchor': 'right',
        'y': 0.115,
        'yanchor': 'top'
    }],
    geo=dict(bgcolor='#F3EFE6'),
    paper_bgcolor='#F3EFE6',
    plot_bgcolor='#F3EFE6',
    margin=dict(l=10, r=10),
    hovermode='x unified',
    height=600,
    width=1200,
    title_x=0.5,
    title_y=0.98,
    title_xanchor="center",
    title_yanchor="top"
)

# Add frames for the animation
frames = []
for i, year in enumerate(years):
    frame = go.Frame(
        data=[
            go.Choropleth(
                locations=df[df['Year'] == year]['Code'],
                z=np.log(df[df['Year'] == year]['Production']),
                colorbar_title="Production",
                zmin=0,
                zmax=np.log(5000000),
                hovertemplate="%{location}<br>Production: %{customdata:,}<extra></extra> tons",
                customdata=df[df['Year'] == year]['Production']
            ),
            go.Bar(
                x=df[df['Year'] == year].sort_values(
                    by='Production', ascending=False)['Entity'],
                y=df[df['Year'] == year].sort_values(
                    by='Production', ascending=False)['Production'],
                hovertemplate="%{x}<br>Production: %{y:,}<extra></extra> tons"
            )
        ],
        name=f'frame_{year}'
    )
    frames.append(frame)

fig.frames = frames

# Show the figure
fig.show()

# Save the figure as an HTML file
pio.write_html(fig, file='map_bar_animation.html', auto_open=False)

/Users/nathanbian/mambaforge/envs/anly503/lib/python3.10/site-packages/pandas/core/arraylike.py:402: RuntimeWarning:

divide by zero encountered in log



In [69]:
import numpy as np
import pandas as pd
import plotly.graph_objects as go

df = data

years = df['Year'].unique()
colors = ["#527A18", "#678D38", "#E9BA4E", "#BF8C31", "#6E3D19"]
custom_scale = [[i/(len(colors)-1), colors[i]] for i in range(len(colors))]

fig_dict = {
    "data": [],
    "layout": {},
    "frames": []
}

# Define the layout
fig_dict["layout"]["title"] = "Coffee Production by Country"
fig_dict["layout"]["width"] = 1200
fig_dict["layout"]["height"] = 600
fig_dict["layout"]["geo"] = {"bgcolor": '#F3EFE6'}
fig_dict["layout"]["paper_bgcolor"] = '#F3EFE6'
fig_dict["layout"]["plot_bgcolor"] = '#F3EFE6'

# Create the slider
sliders_dict = {
    "active": 0,
    "yanchor": "top",
    "xanchor": "left",
    "currentvalue": {
        "font": {"size": 20},
        "prefix": "Year:",
        "visible": True,
        "xanchor": "right"
    },
    "transition": {"duration": 300, "easing": "cubic-in-out"},
    "pad": {"b": 10, "t": 50},
    "len": 0.9,
    "x": 0.1,
    "y": 0,
    "steps": []
}

# Add Choropleth traces
for year in years:
    fig_dict["data"].append(
        go.Choropleth(
            locations=df[df["Year"] == year]["Code"],
            z=np.log(df[df["Year"] == year]["Production"]),
            colorbar=dict(
                title="Production",
                x=0.45,
                xanchor='left',
                y=0.55,
                yanchor='middle'
            ),
            visible=False,
            zmin=0,
            zmax=np.log(5000000),
            colorscale=custom_scale,
            hovertemplate="%{location}<br>Production: %{customdata:,}<extra></extra> tons",
            customdata=df[df["Year"] == year]["Production"]
        )
    )

# Add bar traces for each year
for year in years:
    df_year_sorted = df[df["Year"] == year].sort_values("Production", ascending=False)
    df_year_sorted = df_year_sorted.drop(df_year_sorted[df_year_sorted['Entity'] == 'World'].index)
    fig_dict["data"].append(
        go.Bar(
            x=df_year_sorted["Entity"],
            y=df_year_sorted["Production"] / df_year_sorted["Production"].max(),
            visible=False,
            hovertemplate="Country: %{x}<br>Production: %{y:,}<extra></extra> tons",
            width=1
        )
    )

# Make the first choropleth and bar plot trace visible
fig_dict["data"][0].visible = True
fig_dict["data"][len(years)].visible = True

# Create frames for the animation
for i, year in enumerate(years):
    frame = {"data": [], "name": str(year)}
    # Choropleth frame
    frame["data"].append(
        go.Choropleth(
            locations=df[df["Year"] == year]["Code"],
            z=np.log(df[df["Year"] == year]["Production"]),
            zmin=0,
            zmax=np.log(5000000),
            colorscale=custom_scale,
            hovertemplate="%{location}<br>Production: %{customdata:,}<extra></extra> tons",
            customdata=df[df["Year"] == year]["Production"]
        )
    )

    # Bar plot frame
    df_year_sorted = df[df["Year"] == year].sort_values("Production", ascending=False)
    df_year_sorted = df_year_sorted.drop(df_year_sorted[df_year_sorted['Entity'] == 'World'].index)
    frame["data"].append(
        go.Bar(
            x=df_year_sorted["Entity"],
            y=df_year_sorted["Production"] / df_year_sorted["Production"].max(),
            hovertemplate="Country: %{x}<br>Production: %{y:,}<extra></extra> tons",
            width=1
        )
    )

    fig_dict["frames"].append(frame)
    slider_step = {"args": [
        [str(year)],
        {"visible": [False] * (2 * len(years)), 
        "frame": {"duration": 300, "redraw": True},
        "mode": "immediate",
        "transition": {"duration": 300}}
    ],
        "label": str(year),
        "method": "animate"}
    # slider_step["args"][1]["visible"][i] = True
    # slider_step["args"][1]["visible"][i + len(years)] = True
    sliders_dict["steps"].append(slider_step)

fig_dict["layout"]["sliders"] = [sliders_dict]
fig_dict["layout"]["updatemenus"] = [
    {
        "buttons": [
            {
                "args": [[f"{year}" for year in years],{"frame": {"duration": 500, "redraw": True},
                                "fromcurrent": True, "transition": {"duration": 300,
                                                                    "easing": "quadratic-in-out"}}],
                "label": "Play",
                "method": "animate"
            },
            {
                "args": [[f"{year}" for year in years], {"frame": {"duration": 0, "redraw": True},
                                  "mode": "immediate",
                                  "transition": {"duration": 0}}],
                "label": "Pause",
                "method": "animate"
            }
        ],
        "direction": "left",
        "pad": {"r": 10, "t": 87},
        "showactive": False,
        "type": "buttons",
        "x": 0.1,
        "xanchor": "right",
        "y": 0,
        "yanchor": "top"
    }
]

fig = go.Figure(fig_dict)

# Set the domain for each subplot
fig.update_layout(
    xaxis=dict(domain=[0.55, 1]),
    yaxis=dict(domain=[0, 1]),
    geo=dict(domain=dict(x=[0, 0.45], y=[0, 1]), projection=dict(type="equirectangular")),
    
    annotations=[
        dict(text="World Map", x=0.225, y=1.03, xref="paper", yref="paper",
             showarrow=False, font=dict(size=16)),
        dict(text="Top Countries", x=0.775, y=1.03, xref="paper", yref="paper",
             showarrow=False, font=dict(size=16))
    ]
)

fig.show()


c:\Users\jasonluo\miniconda3\envs\anly503\lib\site-packages\pandas\core\arraylike.py:402: RuntimeWarning:

divide by zero encountered in log



In [70]:
df = df[df["Entity"]!="World"]

# Create a subplot grid with 1 row and 2 columns
fig = sp.make_subplots(rows=1, cols=2, specs=[[{'type': 'choropleth'}, {'type': 'bar'}]],
                       subplot_titles=('World map', 'Coffee Production by Country'))

years = df['Year'].unique()

colors = ["#527A18", "#678D38", "#E9BA4E", "#BF8C31", "#6E3D19"]

custom_scale = [[i/(len(colors)-1), colors[i]] for i in range(len(colors))]

# Add Choropleth traces
for year in years:
    fig.add_trace(
        go.Choropleth(
            uid=f"world_{year}",
            locations=df[df["Year"] == year]["Code"],
            z=np.log(df[df["Year"] == year]["Production"]),
            colorbar=dict(
                title="Production",
                x=0.45,
                xanchor='left',
                y=0.55,
                yanchor='middle'
            ),
            visible=False,
            zmin=0,
            zmax=np.log(5000000),
            colorscale=custom_scale,
            hovertemplate="%{location}<br>Production: %{customdata:,}<extra></extra> tons",
            customdata=df[df["Year"] == year]["Production"]
        ), row=1, col=1
    )

# Add bar traces for each year
for year in years:
    # Sort the data frame by production in descending order
    df_year_sorted = df[df["Year"] == year].sort_values("Production", ascending=False)
    
    fig.add_trace(
        go.Bar(
            uid=f"bar_{year}",
            x=df[df['Year'] == year].sort_values(
                by='Production', ascending=False)['Entity'],
            y=df[df['Year'] == year].sort_values(
                by='Production', ascending=False)['Production'],
            visible=False,
            text=df_year_sorted["Production"],
            textposition='auto',
            hovertemplate="Country: %{x}<br>Production: %{y:,}<extra></extra> tons",
            width=0.8  # Make the bars wider
        ), row=1, col=2
    )

fig.update_yaxes(range=[0, max(df["Production"]) * 1.1], row=1, col=2)
# Make the first choropleth and bar plot trace visible
fig.data[0].visible = True
fig.data[len(years)].visible = True

frames = []

for year in years:
    frame = go.Frame(
        name=f"{year}",
        data=[
            go.Choropleth(
                locations=df[(df["Year"] == year)]["Code"],
                z=np.log(df[(df["Year"] == year)]["Production"]),
                customdata=df[(df["Year"] == year)]["Production"],
                hovertemplate="%{location}<br>Production: %{customdata:,}<extra></extra> tons",
                colorscale=custom_scale
            )
        ]
    )
    frames.append(frame)
for year in years:
    frame = go.Frame(
        name=f"{year}",
        data=[ 
            go.Bar(
                x=df_year_sorted["Entity"],
                y=df_year_sorted["Production"],
                text=df_year_sorted["Production"],
                textposition='auto',
                hovertemplate="Country: %{x}<br>Production: %{y:,}<extra></extra> tons",
                width=0.8
            )
        ]
    )
    frames.append(frame)
steps = []
for i, year in enumerate(years):
    step = dict(
        method="animate",
        args=[[f"year"],{"visible": [False] * (2 * len(years)), 
               'frame': {'duration': 300, 'redraw': False},
                'mode': 'immediate',
                'transition': {'duration': 300}}],
        label=f"{year}"
    )
    step["args"][1]["visible"][i] = True
    step["args"][1]["visible"][i + len(years)] = True
    steps.append(step)
    
# Define the slider
sliders = [dict(
    active=0,
    currentvalue={"prefix": "Year: "},
    steps=steps,
    pad={"t": 50}
)]

fig.update(frames=frames),
# Update the layout with the slider and animation settings
fig.update_layout(
    sliders=sliders,
    updatemenus=[{
        'buttons': [
            {
                'args': [[f"{year}" for year in years], {'frame': {'duration': 300, 'redraw': False},
                         'fromcurrent': True, 'transition': {'duration': 300, 'easing': 'quadratic-in-out'}}],
                'label': 'Play',
                'method': 'animate'
            },
            {
                'args': [[f"{year}" for year in years], {'frame': {'duration': 0, 'redraw': False}, 'mode': 'immediate',
                'transition': {'duration': 0}}],
                'label': 'Pause',
                'method': 'animate'
            }
        ],
        'direction': 'left',
        'pad': {'r': 10, 't': 87},
        'showactive': False,
        'type': 'buttons',
        'x': 0.16,
        'xanchor': 'right',
        'y': 0.115,
        'yanchor': 'top'
    }],
    geo=dict(bgcolor='#F3EFE6'),
    paper_bgcolor='#F3EFE6',
    plot_bgcolor='#F3EFE6',
    margin=dict(l=10, r=10),
    hovermode='x unified',
    height=600,
    width=1200,
    title_x=0.5,
    title_y=0.98,
    title_xanchor="center",
    title_yanchor="top"
)
fig.show() 


In [133]:
import pandas as pd
import pycountry

# Assuming your dataset is in a pandas DataFrame called 'df'
# Make sure the columns are named 'Year', 'Entity', 'Code', 'Production'

def convert_country_name_to_code(country_name):
    try:
        country = pycountry.countries.get(name=country_name)
        if country is not None:
            return int(country.numeric)
        else:
            return None
    except:
        return None
df = data.copy()
# Convert country names in the 'Entity' column to ISO-3166-1 numeric codes
df['Code'] = df['Entity'].apply(convert_country_name_to_code)

# Remove rows with missing or invalid country codes
df.dropna(subset=['Code'], inplace=True)

# Convert the numeric codes to integers
df['id'] = df['Code'].astype(int)

df = df[df['Production'].notna() & (df['Production'] > 0)]

df.to_csv('temperal.csv')

In [132]:
import altair as alt
from vega_datasets import data as vega_data
import pandas as pd
import altair as alt
alt.data_transformers.disable_max_rows()

# Create a slider for the years
year_slider = alt.binding_range(min=1961, max=2021, step=1)
year_select = alt.selection_single(name='Year', fields=['Year'], bind=year_slider, init={'Year': df['Year'].min()})

source = alt.topo_feature(vega_data.world_110m.url, 'countries')
# Create the choropleth chart
choropleth = alt.Chart(source).mark_geoshape(
    stroke='white',
    strokeWidth=1
).encode(
    color='Production:Q',
    tooltip=['Entity:N', 'Production:Q']
).add_selection(
    year_select
).transform_filter(
    year_select
).transform_lookup(
    lookup='id',
    from_=alt.LookupData(df, key='id', fields=['Entity', 'Production'])
).project(
    'equirectangular'
).properties(
    width=800,
    height=450,
    title='Coffee Production by Country'
)

# Create the bar chart
bar_chart = alt.Chart(df).mark_bar().encode(
    x=alt.X('Entity:N', sort='-y', title='Country'),
    y=alt.Y('Production:Q', title='Coffee Production'),
    tooltip=['Entity:N', 'Production:Q']
).properties(
    width=500,
    height=300,
    title='Top Coffee Producing Countries'
).add_selection(
    year_select
).transform_filter(
    year_select
).transform_window(
    rank='rank(Production)',
    sort=[alt.SortField('Production', order='descending')]
).transform_filter(
    alt.datum.rank <= 20
)

# Combine the charts horizontally
combined_chart = alt.hconcat(choropleth, bar_chart).configure_view(
    strokeWidth=0
)
combined_chart

combined_chart.save('combined_chart.html')


/Users/nathanbian/mambaforge/envs/anly503/lib/python3.10/site-packages/altair/utils/core.py:317: FutureWarning:

iteritems is deprecated and will be removed in a future version. Use .items instead.

